# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# less than 10 documents,
id2word = corpora.Dictionary(data)
id2word.filter_extremes(no_below = 4)

In [11]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [12]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [13]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [14]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [15]:
ldaseq.print_topics(time=0) # at timeslice 1, those are the topics

[[('bound', 0.025707696740514433),
  ('algorithm', 0.02531153079920694),
  ('learning', 0.016168781080329542),
  ('online', 0.01356320028214897),
  ('problem', 0.0108963245089207),
  ('regret', 0.010017143579771048),
  ('distribution', 0.008875384078933667),
  ('setting', 0.008611141102698871),
  ('case', 0.008548977954462994),
  ('show', 0.00846927518350943),
  ('complexity', 0.008274693325397299),
  ('time', 0.008245846476016316),
  ('sample', 0.008191852340177606),
  ('result', 0.007069793868842767),
  ('active', 0.006884717427104161),
  ('number', 0.006532811015425304),
  ('query', 0.006202386848818613),
  ('information', 0.006180243074726975),
  ('rate', 0.00574641685488749),
  ('lower', 0.005604267519261272)],
 [('learning', 0.02222323674878976),
  ('algorithm', 0.021110330686127086),
  ('policy', 0.018570930280509323),
  ('problem', 0.018385784293139074),
  ('function', 0.013416772205341487),
  ('state', 0.012663361747074666),
  ('method', 0.010754106557056164),
  ('approach', 0

In [16]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('bound', 0.025707696740514433),
  ('algorithm', 0.02531153079920694),
  ('learning', 0.016168781080329542),
  ('online', 0.01356320028214897),
  ('problem', 0.0108963245089207),
  ('regret', 0.010017143579771048),
  ('distribution', 0.008875384078933667),
  ('setting', 0.008611141102698871),
  ('case', 0.008548977954462994),
  ('show', 0.00846927518350943),
  ('complexity', 0.008274693325397299),
  ('time', 0.008245846476016316),
  ('sample', 0.008191852340177606),
  ('result', 0.007069793868842767),
  ('active', 0.006884717427104161),
  ('number', 0.006532811015425304),
  ('query', 0.006202386848818613),
  ('information', 0.006180243074726975),
  ('rate', 0.00574641685488749),
  ('lower', 0.005604267519261272)],
 [('bound', 0.025779820618181473),
  ('algorithm', 0.02538375249610261),
  ('learning', 0.016208405491939467),
  ('online', 0.013594718488907823),
  ('problem', 0.010919161158441146),
  ('regret', 0.010036742901901452),
  ('distribution', 0.008891972591063859),
  ('setting'

In [17]:
ldaseq.print_topic_times(topic=1)

[[('learning', 0.02222323674878976),
  ('algorithm', 0.021110330686127086),
  ('policy', 0.018570930280509323),
  ('problem', 0.018385784293139074),
  ('function', 0.013416772205341487),
  ('state', 0.012663361747074666),
  ('method', 0.010754106557056164),
  ('approach', 0.010590067565726608),
  ('decision', 0.009832620539274904),
  ('value', 0.008368939110354056),
  ('show', 0.008244619455382787),
  ('agent', 0.008057177853786268),
  ('reinforcement', 0.007876881936816545),
  ('optimal', 0.007613549698022464),
  ('optimization', 0.007073757373167806),
  ('reward', 0.006970797293733868),
  ('control', 0.006803857861174566),
  ('action', 0.006194983119362241),
  ('process', 0.006139283938947572),
  ('dynamic', 0.0058253072174663)],
 [('learning', 0.02228146598928538),
  ('algorithm', 0.021164566932728016),
  ('policy', 0.018616260441176775),
  ('problem', 0.0184305067840922),
  ('function', 0.013443888963829665),
  ('state', 0.012689335561264444),
  ('method', 0.010774467574374775),
  

In [18]:
ldaseq.print_topic_times(topic=2)

[[('kernel', 0.0242470966429573),
  ('problem', 0.019351580158033944),
  ('function', 0.01918168436830574),
  ('graph', 0.017379170805520858),
  ('algorithm', 0.016327248582287637),
  ('learning', 0.011244268679751541),
  ('loss', 0.01026642451864029),
  ('show', 0.009794498405979957),
  ('result', 0.008435540841067497),
  ('based', 0.007355626993580574),
  ('classification', 0.007057903041567375),
  ('method', 0.006894230653638729),
  ('ranking', 0.0063368105677937625),
  ('classifier', 0.0061160799724710455),
  ('paper', 0.005899324111951335),
  ('class', 0.005824384293225207),
  ('space', 0.005320731362058389),
  ('new', 0.005054923987086203),
  ('random', 0.005005219124591209),
  ('approach', 0.004954350152487893)],
 [('kernel', 0.024314754591996467),
  ('problem', 0.0193995490448829),
  ('function', 0.019229831254810485),
  ('graph', 0.017422356971655974),
  ('algorithm', 0.01636682933732466),
  ('learning', 0.011267241577239039),
  ('loss', 0.010286227081517928),
  ('show', 0.009

In [19]:
ldaseq.print_topic_times(topic=3)

[[('model', 0.033692359566425654),
  ('network', 0.016130788181781253),
  ('learning', 0.010914001092975368),
  ('human', 0.010127400471145033),
  ('task', 0.01010654135360726),
  ('deep', 0.0075616643998437085),
  ('prediction', 0.00751645186484024),
  ('neural', 0.006913706349160362),
  ('feature', 0.0064034328656320865),
  ('sequence', 0.00610865155924012),
  ('input', 0.006093239775798162),
  ('layer', 0.005950731327060806),
  ('performance', 0.005815605698278109),
  ('show', 0.005775979227568239),
  ('training', 0.0057648770408913),
  ('information', 0.005436582912610697),
  ('result', 0.005307954437659117),
  ('representation', 0.005142480540459499),
  ('architecture', 0.005058366930016075),
  ('two', 0.005016729634016497)],
 [('model', 0.03367942291437308),
  ('network', 0.016082942070801052),
  ('learning', 0.010922366455232951),
  ('human', 0.01017513526575504),
  ('task', 0.010154224102927389),
  ('deep', 0.007590816186195833),
  ('prediction', 0.007545473684721557),
  ('neur

In [20]:
ldaseq.print_topic_times(topic=4)

[[('method', 0.019463568988394346),
  ('algorithm', 0.018081478649900205),
  ('problem', 0.017317193024170657),
  ('matrix', 0.01353140361025935),
  ('sparse', 0.011693904167968644),
  ('function', 0.007946560812263486),
  ('optimization', 0.007604323142769197),
  ('show', 0.007550931975273007),
  ('convex', 0.007503741111871959),
  ('linear', 0.007295638116715557),
  ('convergence', 0.00715731348665998),
  ('analysis', 0.006989168849216488),
  ('regression', 0.0065432993465884895),
  ('gradient', 0.00643042995055216),
  ('result', 0.006308963306107439),
  ('data', 0.006307709862378154),
  ('paper', 0.006154051073204551),
  ('regularization', 0.005738129237963076),
  ('estimation', 0.005281240019854824),
  ('rate', 0.005223452761661037)],
 [('method', 0.01953082929203779),
  ('algorithm', 0.018017032562448645),
  ('problem', 0.017374575657733777),
  ('matrix', 0.013570700428135674),
  ('sparse', 0.01172613306348624),
  ('function', 0.007964211395524876),
  ('optimization', 0.0076207483

In [21]:
ldaseq.print_topic_times(topic=5)

[[('image', 0.05771446324725846),
  ('object', 0.033348370121263717),
  ('model', 0.015856505208038257),
  ('feature', 0.014367662880689356),
  ('visual', 0.013532833663061726),
  ('method', 0.010734864108177119),
  ('approach', 0.010533310010754493),
  ('scene', 0.009987683367765001),
  ('motion', 0.008726713597159408),
  ('recognition', 0.008121122821686139),
  ('detection', 0.008064377153255042),
  ('segmentation', 0.0071825577388608865),
  ('using', 0.006578453186487419),
  ('local', 0.00641743574588539),
  ('video', 0.006288606664501376),
  ('category', 0.005963058480482271),
  ('human', 0.005647592098663569),
  ('propose', 0.005422928152530034),
  ('vision', 0.005086400859281116),
  ('face', 0.005034745526964195)],
 [('image', 0.05766755624276958),
  ('object', 0.033384926074236904),
  ('model', 0.015915669773133898),
  ('feature', 0.014416917718779412),
  ('visual', 0.013577416519546841),
  ('method', 0.01076560489086675),
  ('approach', 0.01056329503705227),
  ('scene', 0.01001

In [22]:
ldaseq.print_topic_times(topic=6)

[[('learning', 0.040172175667800965),
  ('data', 0.0319900307552043),
  ('task', 0.019788142446814858),
  ('method', 0.017667268385565406),
  ('training', 0.015215168738299097),
  ('approach', 0.01423269943040319),
  ('classification', 0.012686587131727755),
  ('label', 0.011724205493643388),
  ('feature', 0.010440648956767233),
  ('word', 0.009953251061250884),
  ('metric', 0.007881648926928895),
  ('document', 0.007539170019018695),
  ('proposed', 0.007297604349042458),
  ('problem', 0.006954210129968059),
  ('representation', 0.006876514751217441),
  ('information', 0.006845708866488617),
  ('model', 0.006820462381583633),
  ('unlabeled', 0.0067003828409967926),
  ('set', 0.006666393377180285),
  ('domain', 0.006458952742861491)],
 [('learning', 0.04028997180545852),
  ('data', 0.03207716291708391),
  ('task', 0.01983199395042524),
  ('method', 0.017704038461639104),
  ('training', 0.015243866885514226),
  ('approach', 0.014259731998817204),
  ('classification', 0.01270974807215394)

In [23]:
ldaseq.print_topic_times(topic=7)

[[('model', 0.048276345160969944),
  ('data', 0.01802361622276291),
  ('inference', 0.015845269848041525),
  ('distribution', 0.014202706779178393),
  ('method', 0.01324169729367809),
  ('process', 0.011264449322440633),
  ('bayesian', 0.00993734618865001),
  ('variable', 0.009382308735033583),
  ('approach', 0.008925135553218048),
  ('latent', 0.008507824199944742),
  ('structure', 0.008032045274423378),
  ('probabilistic', 0.007792857236648679),
  ('prior', 0.006867670052874425),
  ('using', 0.006681459716561482),
  ('parameter', 0.00640724890072039),
  ('gaussian', 0.006327430449458011),
  ('variational', 0.0053223100492298114),
  ('mixture', 0.0053159176684913195),
  ('show', 0.005308149977693282),
  ('based', 0.005226310756444771)],
 [('model', 0.048393628681768684),
  ('data', 0.018078503037866483),
  ('inference', 0.01588984866474504),
  ('distribution', 0.014241861902896297),
  ('method', 0.013277189869714693),
  ('process', 0.011266808344465437),
  ('bayesian', 0.0099599547360

In [24]:
ldaseq.print_topic_times(topic=8)

[[('algorithm', 0.049072606965931846),
  ('data', 0.024112726206012944),
  ('clustering', 0.020883058861773093),
  ('feature', 0.015422170644228229),
  ('problem', 0.013119921698654141),
  ('method', 0.0121026278381293),
  ('tree', 0.010957313529620403),
  ('set', 0.010255789638026978),
  ('cluster', 0.010164857061926883),
  ('large', 0.009582281504821107),
  ('number', 0.008279722935206747),
  ('show', 0.007433775009340466),
  ('paper', 0.006319192173658068),
  ('time', 0.0062905076259845575),
  ('selection', 0.0062184395531717064),
  ('approach', 0.006180681303584267),
  ('accuracy', 0.006053220673163842),
  ('cost', 0.005978190084958121),
  ('datasets', 0.005602873136204073),
  ('application', 0.005432202288719394)],
 [('algorithm', 0.049235308760598534),
  ('data', 0.024175845310285004),
  ('clustering', 0.020935058742365516),
  ('feature', 0.01545553916870312),
  ('problem', 0.013147128346354918),
  ('method', 0.01212577884650271),
  ('tree', 0.010977394285231042),
  ('set', 0.010

In [25]:
ldaseq.print_topic_times(topic=9)

[[('neural', 0.016323883224805102),
  ('neuron', 0.014587681997328726),
  ('stimulus', 0.011757533297256683),
  ('network', 0.01159275504913797),
  ('model', 0.011161270761105584),
  ('activity', 0.010680663490287463),
  ('brain', 0.009555515979306784),
  ('response', 0.009410605588873668),
  ('spike', 0.00938290273613518),
  ('signal', 0.009199899357689341),
  ('system', 0.007383059455040637),
  ('show', 0.007286380129434156),
  ('dynamic', 0.006971754291698583),
  ('population', 0.00662447292140473),
  ('information', 0.006571290749969861),
  ('input', 0.00615966184093829),
  ('pattern', 0.00567230509240929),
  ('sensory', 0.005188072046899472),
  ('functional', 0.005056648850913657),
  ('cell', 0.0049084216713611815)],
 [('neural', 0.01618878151878712),
  ('neuron', 0.014669691242681185),
  ('stimulus', 0.011814018114464322),
  ('network', 0.01153032365304463),
  ('model', 0.011203343600315493),
  ('activity', 0.010728457953700121),
  ('brain', 0.009595037774922833),
  ('response', 

In [26]:
# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[2.07900208e-04 2.07900208e-04 2.07900208e-04 4.19126565e-01
 2.07900208e-04 2.07900208e-04 2.07900208e-04 4.84801858e-01
 2.07900208e-04 9.46162758e-02]


In [27]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [28]:
ldaseq.print_topic_times(1) # evolution of values for first time slice


[[('learning', 0.02222323674878976),
  ('algorithm', 0.021110330686127086),
  ('policy', 0.018570930280509323),
  ('problem', 0.018385784293139074),
  ('function', 0.013416772205341487),
  ('state', 0.012663361747074666),
  ('method', 0.010754106557056164),
  ('approach', 0.010590067565726608),
  ('decision', 0.009832620539274904),
  ('value', 0.008368939110354056),
  ('show', 0.008244619455382787),
  ('agent', 0.008057177853786268),
  ('reinforcement', 0.007876881936816545),
  ('optimal', 0.007613549698022464),
  ('optimization', 0.007073757373167806),
  ('reward', 0.006970797293733868),
  ('control', 0.006803857861174566),
  ('action', 0.006194983119362241),
  ('process', 0.006139283938947572),
  ('dynamic', 0.0058253072174663)],
 [('learning', 0.02228146598928538),
  ('algorithm', 0.021164566932728016),
  ('policy', 0.018616260441176775),
  ('problem', 0.0184305067840922),
  ('function', 0.013443888963829665),
  ('state', 0.012689335561264444),
  ('method', 0.010774467574374775),
  

In [29]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.9245512832093135
CV1 0.4391480483059283
U_Mass2 -1.923795083713312
CV2 0.43914804830592835
U_Mass3 -1.9063331453922387
CV3 0.4364629182084527
U_Mass4 -1.8980217117341707
CV4 0.43400561755878025
U_Mass5 -1.908747322485878
CV5 0.4281963648199065
U_Mass6 -1.8752132116206908
CV6 0.4268210689359685
U_Mass7 -1.8625953671142383
CV7 0.4319760174893993
U_Mass8 -1.8766597040633506
CV8 0.4383820053455675
U_Mass9 -1.8564411785621373
CV9 0.43447021977279254
U_Mass10 -1.8259749057372505
CV10 0.4346249692017124
U_Mass11 -1.8339641665983344
CV11 0.43924292914626467
U_Mass12 -1.884197762594026
CV12 0.44335213474473995


In [30]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/